In [7]:
# Comprehensive Guide to Evaluating Language Models (LLMs) with Python

# Install necessary libraries
# !pip install numpy pandas scikit-learn rouge-score nltk detoxify lm-eval matplotlib

import os
import warnings
from sklearn.metrics import f1_score
from rouge_score import rouge_scorer
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from detoxify import Detoxify

# Example dataset for evaluation
gold_standard = [
    {"query": "What is 2 + 2?", "correct_answer": "4"},
    {"query": "Who wrote Macbeth?", "correct_answer": "William Shakespeare"},
    {"query": "What is the boiling point of water?", "correct_answer": "100°C"}
]

model_outputs = [
    {"query": "What is 2 + 2?", "output": "4"},
    {"query": "Who wrote Macbeth?", "output": "Charles Dickens"},
    {"query": "What is the boiling point of water?", "output": "100°C"}
]

texts = [
    "This is a friendly and respectful comment.",
    "This is a hateful and offensive comment."
]

# --- 1. Hallucination Reduction Rate (HRR)
def calculate_hrr(baseline_outputs, validated_outputs):
    hallucinations_reduced = sum(
        1 for base, valid in zip(baseline_outputs, validated_outputs)
        if base.get("is_hallucination") and not valid.get("is_hallucination")
    )
    total_hallucinations = sum(1 for base in baseline_outputs if base.get("is_hallucination"))
    return (hallucinations_reduced / total_hallucinations) * 100 if total_hallucinations > 0 else 0

# Example HRR usage
baseline_outputs = [
    {"query": "What is the boiling point of water?", "output": "50°C", "is_hallucination": True},
    {"query": "Who wrote Hamlet?", "output": "Charles Dickens", "is_hallucination": True}
]
validated_outputs = [
    {"query": "What is the boiling point of water?", "output": "100°C", "is_hallucination": False},
    {"query": "Who wrote Hamlet?", "output": "William Shakespeare", "is_hallucination": False}
]
hrr_score = calculate_hrr(baseline_outputs, validated_outputs)
print(f"Hallucination Reduction Rate (HRR): {hrr_score:.2f}%")
print("This score reflects the percentage of hallucinations corrected by the model. A higher value indicates fewer factual errors.")

# --- 2. Logical Consistency Score (LCS)
def calculate_lcs(responses):
    consistent_responses = sum(1 for response in responses if response.get("is_consistent"))
    return (consistent_responses / len(responses)) * 100

# Example LCS usage
responses = [
    {"query": "If A > B and B > C, is A > C?", "output": "Yes", "is_consistent": True},
    {"query": "Is it possible for a square to have three sides?", "output": "No", "is_consistent": True}
]
lcs_score = calculate_lcs(responses)
print(f"Logical Consistency Score (LCS): {lcs_score:.2f}%")
print("This score measures logical reasoning accuracy. A higher value suggests the model maintains logical coherence.")

# --- 3. Response Accuracy (RA)
def calculate_ra(gold_standard, model_outputs):
    correct_responses = sum(
        1 for gold, output in zip(gold_standard, model_outputs)
        if gold["correct_answer"] == output["output"]
    )
    return (correct_responses / len(gold_standard)) * 100

ra_score = calculate_ra(gold_standard, model_outputs)
print(f"Response Accuracy (RA): {ra_score:.2f}%")
print("Response Accuracy measures correctness in providing factual answers. A higher value means more accurate answers.")

# --- 4. Exact Match (EM)
def exact_match(prediction, target):
    return prediction == target

em_score = exact_match("Paris", "Paris")
print(f"Exact Match (EM): {em_score}")
print("Exact Match evaluates if the prediction exactly matches the reference.")

# --- 5. F1 Score
def calculate_f1(predictions, targets):
    return f1_score(targets, predictions, average="binary")

predictions = [1, 0, 1, 1]
targets = [1, 0, 0, 1]
print(f"F1 Score: {calculate_f1(predictions, targets):.2f}")
print("F1 Score balances precision and recall. Higher values suggest fewer false positives and negatives.")

# --- 6. ROUGE
def calculate_rouge(prediction, target):
    scorer = rouge_scorer.RougeScorer(['rouge1', 'rougeL'], use_stemmer=True)
    return scorer.score(target, prediction)

rouge_scores = calculate_rouge("The cat sat on the mat.", "The cat is on the mat.")
print("ROUGE Scores:", rouge_scores)
print("ROUGE measures text similarity. High precision and recall suggest strong alignment with reference.")

# --- 7. BLEU
def calculate_bleu(prediction, target):
    reference = [target.split()]
    candidate = prediction.split()
    smoothing_function = SmoothingFunction().method1
    return sentence_bleu(reference, candidate, smoothing_function=smoothing_function)

bleu_score = calculate_bleu("The cat is on the mat.", "The cat sat on the mat.")
print(f"BLEU Score: {bleu_score:.2f}")
print("BLEU evaluates translation quality. Smoothing addresses low n-gram overlap warnings.")

# --- 8. Toxicity Detection
def detect_toxicity(text):
    model = Detoxify('original')
    return model.predict(text)

for text in texts:
    print(f"Toxicity for '{text}': {detect_toxicity(text)}")
print("Toxicity scores indicate harmful content. Lower scores are preferable for ethical AI.")

from collections import Counter

def calculate_diversity(text, n=2):
    words = text.split()
    ngrams = [' '.join(words[i:i+n]) for i in range(len(words)-n+1)]
    total_ngrams = len(ngrams)
    unique_ngrams = len(set(ngrams))
    return unique_ngrams / total_ngrams if total_ngrams > 0 else 0

# Example Data
text = "The quick brown fox jumps over the lazy dog. The quick brown fox repeats."
diversity_score = calculate_diversity(text, n=2)
print(f"Diversity Score (2-grams): {diversity_score:.2f}")


from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

def calculate_coherence(context, response):
    vectorizer = TfidfVectorizer().fit([context, response])
    vectors = vectorizer.transform([context, response])
    return cosine_similarity(vectors[0], vectors[1])[0][0]

# Example Data
context = "What is the capital of France?"
response = "Paris is the capital of France."
coherence_score = calculate_coherence(context, response)
print(f"Coherence Score: {coherence_score:.2f}")


from detoxify import Detoxify

def detect_bias(text):
    model = Detoxify('original')
    predictions = model.predict(text)
    return predictions['toxicity'], predictions['insult']

# Example Data
biased_text = "Men are better leaders than women."
toxicity, insult = detect_bias(biased_text)
print(f"Toxicity Score: {toxicity:.2f}, Insult Score: {insult:.2f}")



def evaluate_knowledge_retention(questions, correct_answers, model_outputs):
    retained = sum(1 for q, a, o in zip(questions, correct_answers, model_outputs) if a == o)
    return retained / len(questions) * 100

# Example Data
questions = ["Who wrote Hamlet?", "What is the capital of Italy?"]
correct_answers = ["William Shakespeare", "Rome"]
model_outputs = ["William Shakespeare", "Rome"]  # Outputs from the model
knowledge_retention_score = evaluate_knowledge_retention(questions, correct_answers, model_outputs)
print(f"Knowledge Retention Score: {knowledge_retention_score:.2f}%")

Hallucination Reduction Rate (HRR): 100.00%
This score reflects the percentage of hallucinations corrected by the model. A higher value indicates fewer factual errors.
Logical Consistency Score (LCS): 100.00%
This score measures logical reasoning accuracy. A higher value suggests the model maintains logical coherence.
Response Accuracy (RA): 66.67%
Response Accuracy measures correctness in providing factual answers. A higher value means more accurate answers.
Exact Match (EM): True
Exact Match evaluates if the prediction exactly matches the reference.
F1 Score: 0.80
F1 Score balances precision and recall. Higher values suggest fewer false positives and negatives.
ROUGE Scores: {'rouge1': Score(precision=0.8333333333333334, recall=0.8333333333333334, fmeasure=0.8333333333333334), 'rougeL': Score(precision=0.8333333333333334, recall=0.8333333333333334, fmeasure=0.8333333333333334)}
ROUGE measures text similarity. High precision and recall suggest strong alignment with reference.
BLEU Sco

In [2]:
# --- 9. Using `lm-evaluation-harness`
try:
    from lm_eval.evaluator import simple_evaluate
    results = simple_evaluate(
        model="hf",  # Use Hugging Face AutoModel
        model_args="pretrained=gpt2",  # Specify the pretrained model
        tasks=["lambada_openai", "piqa"],  # Tasks to evaluate
       #device="cpu",  # Force evaluation on CPU
    )
    print("LM Evaluation Results:", results)
    print("These results summarize model performance on standard benchmarks.")
except ImportError as e:
    warnings.warn("Ensure `lm-eval` is properly installed for this step.")
except AssertionError as e:
    print("Error:", e)
    print("Ensure your PyTorch installation matches your hardware capabilities (CPU or GPU).")


INFO:lm-eval:Setting random seed to 0 | Setting numpy seed to 1234 | Setting torch manual seed to 1234 | Setting fewshot manual seed to 1234
INFO:lm-eval:Initializing hf model, with arguments: {'pretrained': 'gpt2'}
INFO:lm-eval:Using device 'cuda'
INFO:lm-eval:Using model type 'default'
INFO:lm-eval:Model parallel was set to False, max memory was not set, and device map was set to {'': 'cuda'}
INFO:lm-eval:Building contexts for piqa on rank 0...
100%|██████████| 1838/1838 [00:01<00:00, 1010.09it/s]
INFO:lm-eval:Building contexts for lambada_openai on rank 0...
100%|██████████| 5153/5153 [00:10<00:00, 489.71it/s]
INFO:lm-eval:Running loglikelihood requests
Running loglikelihood requests: 100%|██████████| 8829/8829 [02:27<00:00, 59.81it/s]


bootstrapping for stddev: perplexity


100%|██████████| 100/100 [00:41<00:00,  2.44it/s]


LM Evaluation Results: {'results': {'lambada_openai': {'alias': 'lambada_openai', 'perplexity,none': 40.055420838696435, 'perplexity_stderr,none': 1.4787256351663185, 'acc,none': 0.32563555210556955, 'acc_stderr,none': 0.00652867895783563}, 'piqa': {'alias': 'piqa', 'acc,none': 0.6289445048966268, 'acc_stderr,none': 0.011271222398600666, 'acc_norm,none': 0.6251360174102285, 'acc_norm_stderr,none': 0.01129456580561892}}, 'group_subtasks': {'lambada_openai': [], 'piqa': []}, 'configs': {'lambada_openai': {'task': 'lambada_openai', 'tag': ['lambada'], 'dataset_path': 'EleutherAI/lambada_openai', 'dataset_name': 'default', 'dataset_kwargs': {'trust_remote_code': True}, 'test_split': 'test', 'doc_to_text': "{{text.split(' ')[:-1]|join(' ')}}", 'doc_to_target': "{{' '+text.split(' ')[-1]}}", 'description': '', 'target_delimiter': ' ', 'fewshot_delimiter': '\n\n', 'num_fewshot': 0, 'metric_list': [{'metric': 'perplexity', 'aggregation': 'perplexity', 'higher_is_better': False}, {'metric': 'ac